In [2]:
flex_title = "EECS_Project"

# digestive system

## Column 1

### digestive system related patients

In [37]:
from ipywidgets import interact
import pandas as pd
import numpy as np
from ipywidgets import interact
import seaborn as sns
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

In [38]:
events = pd.read_csv('event_df.csv')
events = events.iloc[:,1:5]

In [39]:
@interact
def show_patient_events(patient_id = np.unique(events.patient_id.values).tolist(),
                       event_type = np.unique(events.event_type.values).tolist()):
    df = events[events.event_type == event_type]
    return df[df.patient_id == patient_id]

interactive(children=(Dropdown(description='patient_id', options=(68, 117, 188, 236, 303, 404, 439, 441, 452, …

### events embedding

In [40]:
embed = pd.read_csv('embed_df_digestive.csv')
embed['icd_9'] = embed['Unnamed: 0']
embed['icd_9'] = [str(i) for i in embed.icd_9.values]

In [41]:
import plotly.express as px
fig = px.scatter(embed, x='tsne-2d-one', y='tsne-2d-two',text = 'icd_9',size_max = 60)
fig.update_traces(textposition='top center')
fig.update_layout(
    height=800,
    title_text='ICD_9 and Drug Code Terminology Embedding'
)
fig.show()


## column 2

### PCA

In [42]:
from ipywidgets import interact
import seaborn as sns
from sklearn.decomposition import PCA
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

In [43]:
df = pd.read_csv('patient_encoding.csv')

In [44]:
df['patient_id']=df['Unnamed: 0']

In [45]:
from sklearn.neighbors import LocalOutlierFactor
clf = LocalOutlierFactor(n_neighbors=30,contamination = 0.005)
pred = clf.fit_predict(df.iloc[:,1:17])

In [46]:
df['status'] = np.where(pred == 1, 'normal','suspicious')

In [47]:
pca = PCA(n_components=3)
pca_result = pca.fit_transform(df.iloc[:,1:17])
df['pca-one'] = pca_result[:,0]
df['pca-two'] = pca_result[:,1] 
df['pca-three'] = pca_result[:,2]

In [48]:
import plotly.express as px

In [49]:
fig = px.scatter_3d(df, x='pca-one', y='pca-two', z='pca-three',
            color='status',hover_data = ['patient_id'])
fig.show()

### t-SNE

In [50]:
df2 = pd.read_csv('t-sne.csv')

In [51]:
df2['status'] = np.where(pred == 1, 'normal','suspicious')

In [52]:
fig = px.scatter(df2, x='tsne-2d-one', y='tsne-2d-two',
            color='status',hover_data = ['patient_id'])
fig.show()

# respiratory/circulatory system related patients

## Column 1

### Circulatory/respiratory system related

In [53]:
events = pd.read_csv('event_df_2.csv')
event = events.iloc[:,1:]

In [26]:
@interact
def show_patient_events(patient_id = np.unique(events.patient_id.values).tolist(),
                       event_type = np.unique(events.event_type.values).tolist()):
    df = events[events.event_type == event_type]
    if event_type == 'Diagnose' or event_type == 'Procedure':
        return df[df.patient_id == patient_id].loc[:,['ADMITTIME','ICD_9','SHORT_TITLE']]
    else:
        return df[df.patient_id == patient_id].loc[:,['ADMITTIME','FORMULARY_DRUG_CD']]

interactive(children=(Dropdown(description='patient_id', options=(9, 26, 28, 31, 32, 36, 37, 41, 42, 49, 63, 6…

### icd-9 embedding

In [54]:
cir_df = pd.read_csv('cir_df.csv')

In [55]:
cir_df['icd_9'] = [str(i) for i in cir_df['icd_9'].values]

In [56]:
import plotly.express as px
fig = px.scatter(cir_df, x='t-SNE_one_d', y='t-SNE_two_d',text = 'icd_9',size_max = 60)
fig.update_traces(textposition='top center')
fig.update_layout(
    height=800,
    title_text='ICD_9 and Drug Code Terminology Embedding'
)
fig.show()


## column 2

### PCA

In [57]:
import plotly.express as px

In [58]:
pca_2 = pd.read_csv('pca_2.csv')

In [59]:
fig = px.scatter_3d(pca_2, x='pca-one', y='pca-two', z='pca-three',
            color='status',hover_data = ['patient_id'])
fig.show()

### t-SNE

In [60]:
t_2 = pd.read_csv('t-SNE_2.csv')

In [61]:
fig = px.scatter(t_2, x='tsne-2d-one', y='tsne-2d-two',
            color='status',hover_data = ['patient_id'])
fig.show()

# Similar Patient Retrieval

In [ ]:
import json
import pandas as pd
import numpy as np
from pandas.io.json import json_normalize
import plotly.express as px
import ipywidgets as widgets
from IPython.display import clear_output, display
import matplotlib.pyplot as plt
from IPython.display import set_matplotlib_formats

# reading the JSON data using json.load()
file ='clean_data_sub-Copy1.json'
with open(file) as train_file:
    dict_train = json.load(train_file)

In [ ]:
total=[]
for patient in dict_train:
    test1=[]
    for num in range (0,len(dict_train[patient])):
        test1.append(dict_train[patient][num]['ICD_9'])
    total.append(test1)

In [ ]:
import gensim
from gensim.models import Word2Vec
model_ted = Word2Vec(sentences=total, size=100, window=20, min_count=1, workers=4, sg=1,iter=100)
#model_ted.wv.most_similar("80124")

In [ ]:
my_dict = dict({})
for idx, key in enumerate(model_ted.wv.vocab):
    my_dict[key] = model_ted.wv[key]

In [ ]:
from fastdtw import fastdtw
from scipy.spatial.distance import euclidean
import matplotlib.pyplot as plt
import numpy as np

In [ ]:
####  Similar Patient Retrieval

In [ ]:
mu_label = widgets.Label(value="similarPatients")
mu_var = widgets.Text(description="Patient", value="4579")
button = widgets.Button(description="Calculate")
widgets.VBox([mu_label, mu_var,button])

In [1]:
out = widgets.Output()

NameError: name 'widgets' is not defined

In [ ]:


def most_similar_patient(change):
    patient= mu_var.value
    with out:
        clear_output()
        d=dict()
        patient_num=[]
        similarity=dict()
        target_patient=dict_train[patient]
        l=[]
        for event in range(0,len(target_patient)):
            icd=target_patient[event]['ICD_9']
            embedding=my_dict[icd]
            l.append(embedding)
        d[patient]=l
        for patients in dict_train:
            m=[]
            patient_event=dict_train[patients]
            for event in range(0,len(patient_event)):
                icd=patient_event[event]['ICD_9']
                embedding=my_dict[icd]
                m.append(embedding)
            d[patients]=m
        for key in d.keys():
            patient_num.append(key)
            distance, path = fastdtw(l,d[key],dist=euclidean)
            similarity[key]=distance
        top5=sorted(similarity.items(), key=lambda x: x[1])[:5]
        print('Patient historical record\n',json_normalize(dict_train[patient]))
        print('Top5 similar patient',top5)

mu_var.observe(most_similar_patient, names="value")
button.on_click(most_similar_patient)  

In [ ]:
most_similar_patient(None)
out

In [ ]:
labels = widgets.Label(value="Compare similiarity of two patients")
Patient_A = widgets.Text(description="Patient A", value="4579")
Patient_B = widgets.Text(description="Patient B", value="2080")
button1 = widgets.Button(description="Calculate")
widgets.VBox([labels,Patient_A,Patient_B,button1])


In [ ]:
out1=widgets.Output()

In [ ]:
def patient_similartiy(Patient_A,Patient_B):
    pa_icd=[]
    pb_icd=[]
    for event in range(0,len(dict_train[Patient_A])):
        icd=dict_train[Patient_A][event]['ICD_9']
        embedding=my_dict[icd]
        pa_icd.append(embedding)
    for event in range(0,len(dict_train[Patient_B])):
        icd=dict_train[Patient_B][event]['ICD_9']
        embedding=my_dict[icd]
        pb_icd.append(embedding)
    distance, path = fastdtw(pa_icd,pb_icd,dist=euclidean)
    index_a,index_b=zip(*path)
    #plot=plt.plot(index_a,index_b, color='k', linewidth=2)
    #fig = go.Figure(data=go.Scatter(x=index_a, y=index_b))
    figures = px.line(x=index_a, y=index_b, labels={'x':'Patient_a', 'y':'Patient_b'})
    return(distance,path,figures.show())


In [ ]:
#def on_value_change(change):
    #Patient_A = Patient_A.value
    #Patient_B= Patient_B.value
#    out.clear_output()
#    with out:
#        display(patient_similartiy(Patient_A.value,Patient_B.value))

#def btn_eventhandler(obj):
#    return(patient_similartiy,{'Patient_A': Patient_A.value, 'Patient_B': Patient_B.value})

def on_button_clicked(change):
      # "linking function with output"
    
    with out1:
        clear_output()
        # what happens when we press the button
        return(patient_similartiy(Patient_A.value,Patient_B.value))
Patient_A.observe(on_button_clicked, names="value")
Patient_B.observe(on_button_clicked, names="value")

button1.on_click(on_button_clicked)

In [ ]:
on_button_clicked(None)
out1

# ICD-9 Retrival

In [ ]:
from sklearn.manifold import TSNE
import matplotlib.pyplot as plt

In [ ]:
icd9_label = widgets.Label(value="Input ICD9")
icd9_var = widgets.Text(description="ICD9", value="80124")
button2= widgets.Button(description="Calculate")
widgets.VBox([icd9_label,icd9_var,button2])

In [ ]:
def display_closestwords_tsnescatterplot(model, word):

    word_labels = [word]

    # get close words
    close_words = model.similar_by_word(word)
    vector_dim = model.vector_size
    # add the vector for each of the closest words to the array
    arr = np.empty((0,vector_dim), dtype='f')
    for wrd_score in close_words:
        wrd_vector = model[wrd_score[0]]
        word_labels.append(wrd_score[0])
        arr = np.append(arr, np.array([wrd_vector]), axis=0)
        
    # find tsne coords for 2 dimensions
    tsne = TSNE(n_components=2, random_state=0)
    np.set_printoptions(suppress=True)
    Y = tsne.fit_transform(arr)

    x_coords = Y[:, 0]
    y_coords = Y[:, 1]
    # display scatter plot
    plt.scatter(x_coords, y_coords)

    for label, x, y in zip(word_labels, x_coords, y_coords):
        plt.annotate(label, xy=(x, y), xytext=(0, 0), textcoords='offset points')
    plt.xlim(x_coords.min()+0.00005, x_coords.max()+0.00005)
    plt.ylim(y_coords.min()+0.00005, y_coords.max()+0.00005)
    plt.show()

In [ ]:
out2 = widgets.Output()

In [ ]:
def on_button_clicked2(change):
    word=icd9_var.value
    model=model_ted
    # "linking function with output"
    
    with out2:
        clear_output()
        # what happens when we press the button
        return(display_closestwords_tsnescatterplot(model,word))
icd9_var.observe(on_button_clicked2, names="value")
button2.on_click(on_button_clicked2)

In [ ]:
on_button_clicked2(None)
out2
#button2.on_click(on_button_clicked2)